In [4]:
import requests
from PIL import Image
from io import BytesIO
import numpy as np
import plotly.graph_objects as go
import os

# Function to convert RGB to Hex
def rgb_to_hex(r, g, b):
    return f"#{r:02X}{g:02X}{b:02X}"

# Function to load an image (local or from URL)
def load_image(input_path):
    if input_path.startswith("http://") or input_path.startswith("https://"):
        print("Loading image from URL...")
        response = requests.get(input_path)
        image = Image.open(BytesIO(response.content))
    else:
        print("Loading image from local path...")
        if os.path.exists(input_path):
            image = Image.open(input_path)
        else:
            raise FileNotFoundError(f"The file at {input_path} does not exist.")
    return image

# Function to process the image and create the plot
def create_image_plot(image):
    # Resize the image to 256x256 to ensure it fits the desired size
    image = image.resize((256, 256))

    # Convert image to RGB (if it's not already)
    if image.mode != 'RGB':
        image = image.convert('RGB')

    # Convert the image to a NumPy array
    image_array = np.array(image)
    height, width, _ = image_array.shape

    # Grid size (since we are working with a 256x256 image, use a grid of 1x1 pixels)
    grid_size = 1

    # Create the figure
    fig = go.Figure()

    # Add the image as a background
    fig.add_layout_image(
        dict(
            source=image,
            x=0,
            y=height,
            xref="x",
            yref="y",
            sizex=width,
            sizey=height,
            xanchor="left",
            yanchor="top",
            layer="below",
        )
    )

    # Create grid and collect RGB values
    grid_x = []
    grid_y = []
    grid_text = []
    grid_colors = []  # To store RGB colors for each square

    # Iterate over the image array in steps of `grid_size` (1 in this case)
    for y in range(0, height, grid_size):
        for x in range(0, width, grid_size):
            # Get the RGB value of each pixel
            r, g, b = image_array[y, x]
            hex_code = rgb_to_hex(r, g, b)

            # Add the grid position and hex code for hover text
            grid_x.append(x)
            grid_y.append(height - y - grid_size)  # Flip Y for plotly
            grid_text.append(f"RGB: ({r},{g},{b})<br>Hex: {hex_code}")
            grid_colors.append(f"rgb({r},{g},{b})")  # Store RGB color for hover

    # Create the grid using scatter plot
    fig.add_trace(go.Scatter(
        x=grid_x, y=grid_y,
        mode="markers",
        marker=dict(size=grid_size, color=grid_colors),
        hoverinfo="text",
        text=grid_text,  # Show hex code and coordinates on hover
    ))

    # Set up axes
    fig.update_xaxes(
        range=[0, width],
        showgrid=False,
        zeroline=False,
    )
    fig.update_yaxes(
        range=[0, height],
        showgrid=False,
        zeroline=False,
        scaleanchor="x",
        scaleratio=1,
    )

    # Update layout
    fig.update_layout(
        title="Hover over the grid to see RGB, Hex Code, and Coordinates",
        margin=dict(l=0, r=0, t=40, b=0),
        hovermode="closest",
    )

    # Show the figure
    fig.show()

def main():
    # Ask the user for the image source (path or URL)
    user_input = input("Please enter the image path or URL: ").strip()

    try:
        # Load the image based on the input (URL or local file path)
        image = load_image(user_input)

        # Create and display the image plot
        create_image_plot(image)

    except Exception as e:
        print(f"Error: {e}")

if __name__ == "__main__":
    main()


Loading image from local path...
